# Using Stock Data to Make Forecasts
## Overview
By using data from twelvedata.com's stock API, I implement the keras library's neural networks to make stock predicitons. 
## Methods
My thoughts on how to best prepare data for the neural network
### Inputs/Outputs Ideas
1. Input raw prices, output raw price predictions
2. Input price derivatives, output percentage growth at different times
3. Input average price over surrounding time periods, output raw price predictions

### Secondary Objectives
1. Input other stock indicators such as P/E, EMACS, etc.


## Importing Libraries

In [70]:
# Import necessary libraries
%matplotlib inline
import matplotlib.pylab as plt
import numpy as np
import keras
from keras.models import Sequential
from keras.layers import Dense, Activation
import sklearn as sk
import requests as rq
import datetime as dt
import json
from os import path, mkdir
from random import choice, sample


## Helper Functions

In [263]:
def getLocalApiKey():
    """Returns my personal api key from a private directory
    """
    f = open("../../../Private/twelveDataApiKey.txt")
    return f.readline()


def print_dict_tree(d, indent=0):
    """Print tree of keys in `dict` object.
    
    Prints the different levels of nested keys in a `dict` object. When there
    are no more dictionaries to key into, prints objects type and byte-size.

    Input
    -----
    d : dict
    """
    for key, value in d.items():
        print('    ' * indent + str(key), end=' ')
        if isinstance(value, dict):
            print(); print_dict_tree(value, indent+1)
        else:
            print(":", str(type(d[key])).split("'")[1], "-", str(len(str(d[key]))))

            
def getStock(apiKey: str, symbol: str, period: str, start_date=None, end_date=None, dp=3):
    '''Returns the json of stock symbol
    
    Requests stock values between start and end date. 
    If no start and end date are selected, it automatically chooses dates 
    from 1 year and 2 months ago.
    
    Input
    -----
    apiKey: your api key
    symbol: stock symbol
    period: the time interval for stock data. Check twelvedata.com for valid inputs
    start_date: yyyy-mm-dd
    end_date: yyyy-mm-dd
    '''
    if not start_date:
        start_date = dt.datetime.today() - dt.timedelta(days=365)
        start_date = str(start_date.strftime('%Y-%m-%d'))
    if not end_date:
        end_date = dt.datetime.today() - dt.timedelta(days=60)
        end_date = str(end_date.strftime('%Y-%m-%d'))
    
    # make API request
    ts = rq.get("https://api.twelvedata.com/time_series?symbol="+symbol+"&interval="+period+"&start_date="+start_date+"&end_date="+end_date+"&dp="+str(dp)+"&apikey="+apiKey).json()
    # Check to see if it is a valid time series. Incorrect values for the 
    # interval or start/end_dates will still return dictionaries, but they will be invalid.
    assert(ts["values"])
    return ts


def saveTS(ts):
    '''Saves a json dict of a stock time series as a .txt
    
    Will create a folder to put saved stock time series in. Future timeseries
    will be placed in this folder as well.
    
    Input
    -----
    ts: timeseries that you want saved
    '''
    symbolName = ts["meta"]["symbol"].replace("/", "")
    if not path.isdir('stockTimeSeries'):
        mkdir("stockTimeSeries")
    with open("stockTimeSeries/"+symbolName+'.txt', 'w') as outfile:
        json.dump(ts, outfile)
        
        
def formatData(ts: dict, backSearch=90, forecastPattern: list = [1, 5, 10, 20, 50]):
    '''Returns time series in a format that is usable by the keras neural network
    
    Returns a list of prices 
    '''
    
    # Ordered list of prices from most old to recent
    prices = [period["close"] for period in ts["values"]]
    prices.reverse()
    
    #print(prices)
    
    
    # Prevents trying to verify prices in unknown time periods
    nPrices = len(prices)
    gap = max(forecastPattern)
    maxIndex = nPrices - gap
    minIndex = backSearch
    indices = [i for i in range(minIndex, maxIndex)]
        
    X = []
    y = []
    
    # Allows us to add prices with their corresponding forecasts to new lists in a random order
    while indices:
        index = choice(indices)
        print("---------\nindex:", index)
        indices.remove(index)
        xBackSearch = []
        for i in range(backSearch):
            xBackSearch.append(float(prices[index-i]))
        X.append(xBackSearch)
        yForecast = []
        for delta in forecastPattern:
            yForecast.append(float(prices[index+delta]))
        y.append(yForecast)
    
    X = np.reshape(X, (-1, backSearch))
    y = np.reshape(y, (-1, len(forecastPattern)))
    # Prints price, followed by forecast
    
    return X, y
    

def splitData(X: list, y: list, ratio=.5):
    '''Returns 4 lists, composed to training and test data
    
    Input
    -----
    X: data for input neurons
    y: data for results
    
    Output
    ------
    '''
    split = int(len(X)*ratio)
    x_training = X[:split]
    y_training = y[:split]
    x_test = X[split:]
    y_test = y[split:]
    return x_training, y_training, x_test, y_test
    

def trainData(x_train, y_train, scalar=False, priceTiming="cls"):
    '''
    descriptioin
    
    Input
    -----
    priceTiming: Can be "avg", which averages closing price over surrounding time periods, or
    "cls", which uses closing price for that time period
    To implement: Averaging over course of day, averaging over course of weeks, etc
    
    Output
    ------
    X: A list of lists containing stock prices from the last 
    90 entries from an arbitrary point in time
    y: a list of lists containing the stock prices a number of 
    days in the future corresponding to theforecast pattern'''
    pass

## Using AAPL stock to train the neural network
It is uncertain whether all stocks behave in the same way. For example, a neural network learning from apple stock 
may not be able to be as accurate when predicting oil stocks, or even other tech sector stocks. However, in order to create the foundation of the neural network, I wanted to use it on a high volume, high market cap, relatively low volatility stock. If I can train it with AAPL stock, I may be able to apply the neural network to other stocks.

In [ ]:
# get and save the aapl stock time series as a .txt
myApiKey = getLocalApiKey()

aaplTS = getStock(myApiKey, "aapl", "1day", start_date="2002-01-01", end_date="2020-9-30")

X, y = formatData(aaplTS, backSearch=90)
x_train, y_train, x_test, y_test = splitData(X, y)
print(x_train[:10])
print()
print(y_train[:10])


---------
index: 4104
41.31 4104
41.43 4103
43.2 4102
44.46 4101
44.56 4100
43.955 4099
43.682 4098
43.535 4097
43.11 4096
43.312 4095
42.513 4094
42.095 4093
43.2 4092
42.903 4091
42.097 4090
41.67 4089
41.945 4088
41.62 4087
42.085 4086
43.193 4085
41.235 4084
42.213 4083
42.818 4082
43.81 4081
43.825 4080
44.505 4079
44.662 4078
44.61 4077
44.993 4076
45.43 4075
44.995 4074
44.235 4073
43.757 4072
44.167 4071
44.205 4070
44.053 4069
43.75 4068
44.53 4067
44.597 4066
44.743 4065
43.875 4064
43.125 4063
42.768 4062
42.963 4061
43.107 4060
43.248 4059
41.842 4058
41.085 4057
40.678 4056
39.103 4055
38.787 4054
39.885 4053
40.757 4052
39.123 4051
40.125 4050
41.945 4049
41.857 4048
41.743 4047
41.99 4046
42.877 4045
42.778 4044
43.555 4043
44.26 4042
44.25 4041
44.615 4040
44.815 4039
44.775 4038
44.048 4037
44.272 4036
43.82 4035
43.572 4034
43.583 4033
43.588 4032
43.75 4031
43.257 4030
43.057 4029
43.065 4028
42.307 4027
42.77 4026
42.65 4025
42.643 4024
43.752 4023
43.752 4022
43.58

12.073 2332
12.103 2331
12.185 2330
12.306 2329
12.447 2328
12.451 2327
12.534 2326
12.516 2325
12.555 2324
12.32 2323
12.114 2322
12.186 2321
12.118 2320
11.81 2319
11.951 2318
11.786 2317
12.337 2316
12.627 2315
12.571 2314
12.381 2313
12.588 2312
12.706 2311
12.691 2310
12.857 2309
12.841 2308
12.576 2307
12.475 2306
12.615 2305
12.434 2304
12.246 2303
12.236 2302
12.093 2301
---------
index: 2643
20.857 2643
20.323 2642
20.518 2641
20.43 2640
20.385 2639
20.789 2638
20.631 2637
20.919 2636
20.979 2635
20.921 2634
20.505 2633
20.412 2632
20.434 2631
20.577 2630
20.399 2629
20.726 2628
20.419 2627
20.409 2626
20.101 2625
20.153 2624
20.035 2623
20.633 2622
20.685 2621
20.438 2620
20.082 2619
20.19 2618
20.377 2617
19.892 2616
20.046 2615
18.942 2614
18.933 2613
19.503 2612
19.756 2611
19.936 2610
20.24 2609
20.376 2608
20.328 2607
20.292 2606
20.339 2605
20.188 2604
20.779 2603
20.928 2602
20.79 2601
20.856 2600
21.536 2599
21.704 2598
21.786 2597
20.01 2596
20.418 2595
20.464 2594
2

24.108 3544
24.335 3543
23.522 3542
23.355 3541
24.997 3540
24.86 3539
25.355 3538
24.075 3537
24.198 3536
24.165 3535
---------
index: 3999
42.537 3999
42.775 3998
42.27 3997
42.835 3996
43.493 3995
43.667 3994
43.97 3993
44.06 3992
43.702 3991
43.562 3990
43.125 3989
42.028 3988
41.722 3987
42.26 3986
41.68 3985
40.763 3984
39.353 3983
39.103 3982
39.275 3981
39.042 3980
39.062 3979
38.995 3978
39.94 3977
40.118 3976
39.97 3975
39.248 3974
39.0 3973
39.138 3972
38.975 3971
38.96 3970
38.825 3969
38.847 3968
38.37 3967
38.62 3966
38.452 3965
38.53 3964
38.32 3963
38.557 3962
38.285 3961
37.638 3960
37.972 3959
38.347 3958
39.018 3957
39.682 3956
39.667 3955
39.97 3954
39.57 3953
39.912 3952
40.215 3951
40.375 3950
39.658 3949
40.315 3948
40.478 3947
40.52 3946
41.013 3945
41.0 3944
40.838 3943
40.728 3942
40.368 3941
39.965 3940
39.818 3939
39.995 3938
39.945 3937
39.303 3936
39.375 3935
39.465 3934
40.237 3933
40.4 3932
39.963 3931
39.37 3930
38.83 3929
40.265 3928
40.02 3927
39.702 

14.995 2839
15.35 2838
15.512 2837
15.56 2836
15.249 2835
15.222 2834
15.114 2833
15.276 2832
15.428 2831
15.35 2830
15.318 2829
15.809 2828
16.146 2827
16.469 2826
16.556 2825
16.497 2824
16.169 2823
16.146 2822
16.232 2821
16.276 2820
15.845 2819
15.446 2818
15.298 2817
15.301 2816
15.638 2815
15.419 2814
15.378 2813
15.202 2812
15.398 2811
15.002 2810
15.374 2809
15.764 2808
15.877 2807
16.035 2806
15.814 2805
16.1 2804
15.931 2803
16.03 2802
16.428 2801
16.434 2800
16.664 2799
16.679 2798
16.711 2797
17.14 2796
16.964 2795
16.722 2794
16.334 2793
16.351 2792
15.797 2791
16.201 2790
16.267 2789
16.315 2788
16.367 2787
16.065 2786
15.71 2785
16.089 2784
18.358 2783
18.028 2782
17.857 2781
17.953 2780
18.075 2779
17.354 2778
17.92 2777
18.582 2776
18.697 2775
18.468 2774
18.761 2773
18.711 2772
18.821 2771
19.361 2770
19.608 2769
19.006 2768
18.2 2767
18.395 2766
18.321 2765
18.577 2764
18.548 2763
18.633 2762
18.797 2761
19.068 2760
---------
index: 1135
1.992 1135
2.036 1134
2.07 11

58.592 4478
58.83 4477
58.967 4476
59.053 4475
57.522 4474
56.757 4473
56.1 4472
56.765 4471
56.752 4470
55.205 4469
54.74 4468
56.147 4467
55.993 4466
54.705 4465
54.972 4464
55.257 4463
54.42 4462
54.68 4461
54.432 4460
55.24 4459
55.693 4458
55.175 4457
54.975 4456
54.688 4455
55.772 4454
55.897 4453
54.175 4452
53.542 4451
53.315 4450
53.32 4449
52.298 4448
51.425 4447
52.185 4446
52.252 4445
51.382 4444
51.04 4443
---------
index: 4289
38.735 4289
38.268 4288
37.5 4287
38.072 4286
38.45 4285
38.327 4284
37.688 4283
36.982 4282
37.065 4281
35.548 4280
39.48 4279
39.435 4278
39.057 4277
39.037 4276
39.292 4275
36.708 4274
37.682 4273
39.208 4272
40.222 4271
41.518 4270
40.985 4269
41.37 4268
42.737 4267
42.275 4266
42.158 4265
42.4 4264
42.123 4263
43.68 4262
44.173 4261
46.205 4260
44.645 4259
44.888 4258
45.235 4257
43.56 4256
43.655 4255
43.072 4254
44.195 4253
44.245 4252
46.465 4251
48.382 4250
47.853 4249
46.7 4248
48.057 4247
48.542 4246
51.118 4245
52.123 4244
52.487 4243
50

...

0.411 509
0.417 508
0.403 507
0.394 506
0.396 505
0.38 504
0.382 503
0.38 502
0.378 501
0.371 500
0.364 499
0.354 498
0.354 497
0.352 496
0.358 495
0.355 494
0.359 493
0.36 492
0.373 491
0.379 490
0.364 489
0.365 488
0.376 487
0.372 486
0.378 485
0.376 484
0.385 483
0.388 482
---------
index: 967
2.141 967
2.054 966
2.057 965
1.945 964
1.979 963
2.037 962
2.004 961
2.028 960
1.988 959
2.005 958
1.962 957
1.865 956
1.909 955
1.929 954
1.919 953
1.759 952
1.842 951
1.799 950
1.832 949
1.846 948
1.885 947
1.92 946
1.944 945
1.915 944
1.869 943
1.824 942
1.909 941
1.923 940
1.9 939
1.854 938
1.861 937
1.9 936
1.88 935
1.829 934
1.781 933
1.772 932
1.815 931
1.836 930
1.832 929
1.778 928
1.739 927
1.743 926
1.651 925
1.652 924
1.675 923
1.663 922
1.637 921
1.634 920
1.645 919
1.635 918
1.634 917
1.638 916
1.637 915
1.654 914
1.684 913
1.652 912
1.703 911
1.646 910
1.571 909
1.549 908
1.565 907
1.523 906
1.535 905
1.525 904
1.544 903
1.543 902
1.527 901
1.523 900
1.564 899
1.571 898
1.558 89

28.983 3253
28.657 3252
28.767 3251
29.733 3250
29.75 3249
29.4 3248
29.657 3247
29.118 3246
29.077 3245
28.667 3244
28.868 3243
28.497 3242
28.545 3241
28.205 3240
27.812 3239
27.425 3238
27.208 3237
27.253 3236
27.175 3235
27.215 3234
27.15 3233
27.35 3232
27.0 3231
26.745 3230
26.835 3229
26.685 3228
26.278 3227
26.305 3226
26.208 3225
25.747 3224
---------
index: 3309
32.197 3309
33.042 3308
33.25 3307
32.375 3306
32.112 3305
32.18 3304
31.958 3303
31.77 3302
31.615 3301
31.22 3300
30.505 3299
29.93 3298
29.733 3297
29.985 3296
29.89 3295
29.663 3294
29.657 3293
29.29 3292
29.725 3291
28.827 3290
27.285 3289
28.275 3288
28.245 3287
28.1 3286
27.388 3285
27.18 3284
26.497 3283
26.705 3282
27.45 3281
27.555 3280
27.312 3279
28.003 3278
27.972 3277
26.938 3276
26.565 3275
26.562 3274
27.333 3273
27.595 3272
28.13 3271
28.478 3270
28.497 3269
28.003 3268
28.135 3267
28.235 3266
27.945 3265
28.163 3264
27.353 3263
26.688 3262
27.058 3261
27.433 3260
27.905 3259
27.987 3258
28.53 3257
28

20.323 2642
20.518 2641
20.43 2640
20.385 2639
20.789 2638
20.631 2637
20.919 2636
20.979 2635
20.921 2634
20.505 2633
20.412 2632
20.434 2631
20.577 2630
20.399 2629
20.726 2628
20.419 2627
20.409 2626
20.101 2625
20.153 2624
20.035 2623
20.633 2622
20.685 2621
20.438 2620
20.082 2619
20.19 2618
20.377 2617
19.892 2616
20.046 2615
18.942 2614
18.933 2613
19.503 2612
19.756 2611
19.936 2610
20.24 2609
20.376 2608
---------
index: 2194
10.115 2194
9.835 2193
9.877 2192
9.651 2191
9.574 2190
9.537 2189
9.408 2188
9.395 2187
9.39 2186
9.208 2185
9.242 2184
9.006 2183
8.94 2182
8.682 2181
8.661 2180
8.629 2179
8.581 2178
8.675 2177
8.569 2176
8.779 2175
8.916 2174
8.924 2173
9.038 2172
8.999 2171
8.844 2170
8.896 2169
8.993 2168
8.935 2167
9.265 2166
9.348 2165
9.289 2164
9.346 2163
9.392 2162
9.355 2161
9.352 2160
9.188 2159
9.218 2158
9.32 2157
9.431 2156
9.26 2155
9.284 2154
9.251 2153
9.08 2152
8.996 2151
8.771 2150
8.925 2149
8.98 2148
9.026 2147
8.993 2146
9.189 2145
9.272 2144
9.217

28.993 3767
28.955 3766
28.798 3765
28.798 3764
28.325 3763
28.487 3762
28.03 3761
27.757 3760
27.487 3759
27.278 3758
27.475 3757
27.372 3756
27.63 3755
27.865 3754
27.892 3753
27.948 3752
27.808 3751
27.95 3750
27.933 3749
27.515 3748
27.487 3747
27.497 3746
26.778 3745
26.427 3744
27.108 3743
26.948 3742
27.72 3741
27.765 3740
27.603 3739
27.21 3738
27.458 3737
27.897 3736
27.872 3735
28.385 3734
28.43 3733
28.62 3732
28.897 3731
29.562 3730
29.413 3729
29.15 3728
29.265 3727
29.28 3726
29.368 3725
29.388 3724
29.407 3723
29.245 3722
29.335 3721
29.075 3720
29.013 3719
28.515 3718
28.472 3717
28.263 3716
28.25 3715
28.13 3714
28.263 3713
28.045 3712
28.487 3711
28.272 3710
28.22 3709
28.177 3708
28.655 3707
28.388 3706
28.392 3705
28.395 3704
28.73 3703
28.892 3702
27.942 3701
26.987 3700
26.36 3699
25.782 3698
---------
index: 3147
23.507 3147
23.37 3146
23.38 3145
23.233 3144
22.995 3143
22.725 3142
22.59 3141
22.57 3140
22.708 3139
22.728 3138
22.965 3137
23.045 3136
23.02 3135
2

28.263 3713
28.045 3712
28.487 3711
28.272 3710
28.22 3709
28.177 3708
28.655 3707
28.388 3706
28.392 3705
28.395 3704
28.73 3703
28.892 3702
27.942 3701
26.987 3700
26.36 3699
25.782 3698
26.38 3697
27.09 3696
26.925 3695
26.933 3694
26.683 3693
26.525 3692
26.5 3691
26.705 3690
26.735 3689
26.892 3688
27.007 3687
27.212 3686
27.128 3685
27.34 3684
27.27 3683
27.305 3682
27.345 3681
27.37 3680
27.045 3679
26.983 3678
27.0 3677
27.202 3676
27.093 3675
26.87 3674
26.468 3673
26.448 3672
26.12 3671
26.513 3670
26.052 3669
26.085 3668
25.737 3667
24.167 3666
24.335 3665
---------
index: 3891
35.568 3891
36.072 3890
36.29 3889
36.647 3888
36.355 3887
37.245 3886
38.748 3885
38.842 3884
38.612 3883
38.482 3882
38.862 3881
38.295 3880
38.19 3879
38.417 3878
38.403 3877
38.467 3876
38.335 3875
38.45 3874
38.498 3873
38.265 3872
38.135 3871
37.562 3870
38.868 3869
38.925 3868
39.025 3867
38.487 3866
38.315 3865
38.498 3864
38.252 3863
37.24 3862
36.632 3861
36.765 3860
36.877 3859
36.645 3858


In [262]:
model = Sequential()
model.add(Dense(20, input_dim=len(x_train[0]), activation = 'relu'))
model.add(Dense(30, activation='relu'))
model.add(Dense(20, activation='relu'))
model.add(Dense(20, activation='relu'))
model.add(Dense(20, activation='relu'))
model.add(Dense(20, activation='relu'))
model.add(Dense(len(y_train[0]), activation='softmax'))

model.compile(optimizer='sgd',
              loss='mse',
              metrics=['accuracy'])

model.fit(x_train, y_train, epochs=500, batch_size=len(x_train//10))

score = model.evaluate(x_test, y_test, batch_size=100)
print("accuracy:", score[1])

Epoch 1/500
1/1 [==============================] - 0s 1ms/step - loss: 4882.8862 - accuracy: 0.0268
Epoch 2/500
1/1 [==============================] - 0s 811us/step - loss: 4882.8867 - accuracy: 0.0268
Epoch 3/500
1/1 [==============================] - 0s 943us/step - loss: 4882.8862 - accuracy: 0.0268
Epoch 4/500
1/1 [==============================] - 0s 837us/step - loss: 4882.8862 - accuracy: 0.0268
Epoch 5/500
1/1 [==============================] - 0s 762us/step - loss: 4882.8867 - accuracy: 0.0268
Epoch 6/500
1/1 [==============================] - 0s 653us/step - loss: 4882.8867 - accuracy: 0.0268
Epoch 7/500
1/1 [==============================] - 0s 805us/step - loss: 4882.8867 - accuracy: 0.0268
Epoch 8/500
1/1 [==============================] - 0s 969us/step - loss: 4882.8862 - accuracy: 0.0268
Epoch 9/500
1/1 [==============================] - 0s 1ms/step - loss: 4882.8867 - accuracy: 0.0268
Epoch 10/500
1/1 [==============================] - 0s 1ms/step - loss: 4882.8862 - ac

1/1 [==============================] - 0s 2ms/step - loss: 4882.8867 - accuracy: 0.0268
Epoch 82/500
1/1 [==============================] - 0s 2ms/step - loss: 4882.8867 - accuracy: 0.0268
Epoch 83/500
1/1 [==============================] - 0s 2ms/step - loss: 4882.8862 - accuracy: 0.0268
Epoch 84/500
1/1 [==============================] - 0s 875us/step - loss: 4882.8862 - accuracy: 0.0268
Epoch 85/500
1/1 [==============================] - 0s 906us/step - loss: 4882.8862 - accuracy: 0.0268
Epoch 86/500
1/1 [==============================] - 0s 1ms/step - loss: 4882.8867 - accuracy: 0.0268
Epoch 87/500
1/1 [==============================] - 0s 1ms/step - loss: 4882.8867 - accuracy: 0.0268
Epoch 88/500
1/1 [==============================] - 0s 1ms/step - loss: 4882.8862 - accuracy: 0.0268
Epoch 89/500
1/1 [==============================] - 0s 875us/step - loss: 4882.8862 - accuracy: 0.0268
Epoch 90/500
1/1 [==============================] - 0s 1ms/step - loss: 4882.8862 - accuracy: 0.02

Epoch 161/500
1/1 [==============================] - 0s 1ms/step - loss: 4882.8867 - accuracy: 0.0268
Epoch 162/500
1/1 [==============================] - 0s 934us/step - loss: 4882.8862 - accuracy: 0.0268
Epoch 163/500
1/1 [==============================] - 0s 874us/step - loss: 4882.8862 - accuracy: 0.0268
Epoch 164/500
1/1 [==============================] - 0s 952us/step - loss: 4882.8867 - accuracy: 0.0268
Epoch 165/500
1/1 [==============================] - 0s 1ms/step - loss: 4882.8862 - accuracy: 0.0268
Epoch 166/500
1/1 [==============================] - 0s 1ms/step - loss: 4882.8862 - accuracy: 0.0268
Epoch 167/500
1/1 [==============================] - 0s 1ms/step - loss: 4882.8867 - accuracy: 0.0268
Epoch 168/500
1/1 [==============================] - 0s 887us/step - loss: 4882.8862 - accuracy: 0.0268
Epoch 169/500
1/1 [==============================] - 0s 806us/step - loss: 4882.8862 - accuracy: 0.0268
Epoch 170/500
1/1 [==============================] - 0s 1ms/step - loss:

1/1 [==============================] - 0s 794us/step - loss: 4882.8867 - accuracy: 0.0268
Epoch 240/500
1/1 [==============================] - 0s 764us/step - loss: 4882.8862 - accuracy: 0.0268
Epoch 241/500
1/1 [==============================] - 0s 2ms/step - loss: 4882.8862 - accuracy: 0.0268
Epoch 242/500
1/1 [==============================] - 0s 1ms/step - loss: 4882.8862 - accuracy: 0.0268
Epoch 243/500
1/1 [==============================] - 0s 1ms/step - loss: 4882.8862 - accuracy: 0.0268
Epoch 244/500
1/1 [==============================] - 0s 1ms/step - loss: 4882.8862 - accuracy: 0.0268
Epoch 245/500
1/1 [==============================] - 0s 1ms/step - loss: 4882.8862 - accuracy: 0.0268
Epoch 246/500
1/1 [==============================] - 0s 1ms/step - loss: 4882.8862 - accuracy: 0.0268
Epoch 247/500
1/1 [==============================] - 0s 759us/step - loss: 4882.8867 - accuracy: 0.0268
Epoch 248/500
1/1 [==============================] - 0s 911us/step - loss: 4882.8862 - acc

1/1 [==============================] - 0s 1ms/step - loss: 4882.8862 - accuracy: 0.0268
Epoch 319/500
1/1 [==============================] - 0s 2ms/step - loss: 4882.8867 - accuracy: 0.0268
Epoch 320/500
1/1 [==============================] - 0s 1ms/step - loss: 4882.8862 - accuracy: 0.0268
Epoch 321/500
1/1 [==============================] - 0s 1ms/step - loss: 4882.8862 - accuracy: 0.0268
Epoch 322/500
1/1 [==============================] - 0s 953us/step - loss: 4882.8862 - accuracy: 0.0268
Epoch 323/500
1/1 [==============================] - 0s 907us/step - loss: 4882.8867 - accuracy: 0.0268
Epoch 324/500
1/1 [==============================] - 0s 2ms/step - loss: 4882.8862 - accuracy: 0.0268
Epoch 325/500
1/1 [==============================] - 0s 960us/step - loss: 4882.8862 - accuracy: 0.0268
Epoch 326/500
1/1 [==============================] - 0s 1ms/step - loss: 4882.8857 - accuracy: 0.0268
Epoch 327/500
1/1 [==============================] - 0s 1ms/step - loss: 4882.8862 - accur

1/1 [==============================] - 0s 2ms/step - loss: 4882.8867 - accuracy: 0.0268
Epoch 398/500
1/1 [==============================] - 0s 1ms/step - loss: 4882.8867 - accuracy: 0.0268
Epoch 399/500
1/1 [==============================] - 0s 852us/step - loss: 4882.8862 - accuracy: 0.0268
Epoch 400/500
1/1 [==============================] - 0s 1ms/step - loss: 4882.8857 - accuracy: 0.0268
Epoch 401/500
1/1 [==============================] - 0s 913us/step - loss: 4882.8862 - accuracy: 0.0268
Epoch 402/500
1/1 [==============================] - 0s 1ms/step - loss: 4882.8862 - accuracy: 0.0268
Epoch 403/500
1/1 [==============================] - 0s 1ms/step - loss: 4882.8867 - accuracy: 0.0268
Epoch 404/500
1/1 [==============================] - 0s 1ms/step - loss: 4882.8867 - accuracy: 0.0268
Epoch 405/500
1/1 [==============================] - 0s 975us/step - loss: 4882.8867 - accuracy: 0.0268
Epoch 406/500
1/1 [==============================] - 0s 1ms/step - loss: 4882.8867 - accur

1/1 [==============================] - 0s 856us/step - loss: 4882.8862 - accuracy: 0.0268
Epoch 477/500
1/1 [==============================] - 0s 826us/step - loss: 4882.8862 - accuracy: 0.0268
Epoch 478/500
1/1 [==============================] - 0s 1ms/step - loss: 4882.8862 - accuracy: 0.0268
Epoch 479/500
1/1 [==============================] - 0s 884us/step - loss: 4882.8862 - accuracy: 0.0268
Epoch 480/500
1/1 [==============================] - 0s 1ms/step - loss: 4882.8862 - accuracy: 0.0268
Epoch 481/500
1/1 [==============================] - 0s 1ms/step - loss: 4882.8862 - accuracy: 0.0268
Epoch 482/500
1/1 [==============================] - 0s 2ms/step - loss: 4882.8862 - accuracy: 0.0268
Epoch 483/500
1/1 [==============================] - 0s 1ms/step - loss: 4882.8862 - accuracy: 0.0268
Epoch 484/500
1/1 [==============================] - 0s 800us/step - loss: 4882.8862 - accuracy: 0.0268
Epoch 485/500
1/1 [==============================] - 0s 851us/step - loss: 4882.8857 - a

### 